# Development

This script is for development of other functions - just for simplicity of execution etc. Later the code should be moved to *football_functions*, and then deleted from here.

## Block 0: Initial packages and definitions

Just a block to define some stuff that we will probably never be changing

In [1]:
# Base packages for running the script
import sys, datetime, pickle

# Set the path and proxy in accordance with our OS
if sys.platform == 'linux':
    HOME_PATH = '/home/andreas/Desktop/Projects/Football/'
    proxy_settings = None
else:
    HOME_PATH = 'c:/Users/amathewl/Desktop/03_Personal_projects/football/'
    proxy_settings = None
    
# Relative paths
html_loc = HOME_PATH + 'Data/01_HTML/'
organ_loc = HOME_PATH + 'Data/00_Organisation/'
story_loc = HOME_PATH + 'Data/02_Stories/'

# Get today's date for various functions
date_today = '2018_01_27'#datetime.datetime.today().strftime('%Y_%m_%d')

## Block 1: HTML function for searching for the full story in different sources

Here we will be developing the functions that will search through the story HTML and pull the story. This should then go into processes as the end process.

This should go as follows:
* First we get the story HTML and feed into a function that will process it
* In this function, there will be something specific for each domain
* We should return the story text
* Then we should get the pickle of the headline back up and save the text

Have to think about how to get the pickle
* Maybe the best way to do it is to directly load the pickle - take its link, then search for the HTML (with a try except) and then save

For now will load in the HTML directly and focus on that - then later design a function for the pickle part

Things to think about when translating away from development
* Harmonisation of names (e.g. story_twitter etc.)
* Proper ordering of things

In [4]:
import parsel as pr
import os
import re

In [5]:
# TO DO
# Should pull some meta data - like author and date
# This could maybe be a separate script - i.e. "get meta data"
# We could update the headline, or include a second one + additional summaries + authors etc

## mirror and mail authors guardian canhave 2
## Skysports get rubbish tagged on at the end
## telegraph is weird
## for daily mail and telegraph should check the encoding on the webpage because getting strange characters


## Have to check //text - for example A rsene wenger story

## Have a weird issue for some stories that individual letters get separated because of how the HTML is set up -
## making us insert full stops in random places
# Could overcome this by joining on a blank space - and then regexing for strings that have aAa type pattern
# to insert that again with a full stop

def get_story(story_html, domain):
    '''
    Function that should return the story text of an article's HTML - unique for each source
    '''
    
    sel = pr.Selector(story_html)
    
    if domain == 'bbc': 
        # Get the main text - I think this will eat up some match report details, but could remove later, could be useful
        story_body = sel.xpath('//p//text() | //figcaption/text()').extract()
        story_date = sel.xpath('//meta[@property = "rnews:datePublished"]/@content').extract_first()
        # Join it all up
        story_text = ''.join(story_body)
        
        story_author = sel.xpath('//p[@class = "gel-long-primer"]/text()').extract_first()
        story_twitter = ''
        story_keywords = ['']
        
    elif domain == 'dailymail':
        # Daily mail has a lot of meta information, including various summaries and twitter summaries
        # Might be worth it to revisit to try and get some more - thing is that everything
        # Would get really source specific
        # Get the text parts including the image captions and bold headlines in order
        xpath_string = '//p[@class = "mol-para-with-font" or @class = "imageCaption"]//text() | //div[@class = "lc-title-container"]/span/b/text() | //ul[@class= "mol-bullets-with-font"]//text()'
        story_body = sel.xpath(xpath_string).extract()
        story_author = sel.xpath('//meta[@property = "article:author"]/@content').extract_first()
        story_date = sel.xpath('//meta[@property = "article:published_time"]/@content').extract_first()
        story_twitter = sel.xpath('//meta[@property = "twitter:description"]/@content').extract_first()
        
        story_text = ''.join(story_body)
        
        story_keywords = ['']
        
    elif domain == 'theguardian':
        # Found meta data with tags of teams
        story_author = sel.xpath('//meta[@property = "article:author"]/@content').extract_first()
        story_date = sel.xpath('//meta[@property = "article:published_time"]/@content').extract_first()   
        story_keywords = sel.xpath('//meta[@name = "keywords"]/@content').extract()
        # There are <p> parts in comments - but all have the form
        story_body = sel.xpath('//p[not(ancestor::div[contains(@class, "comment")])]//text()').extract()
        
        story_text = ''.join(story_body)
        
        story_twitter = ''
        
    elif domain == 'mirror':
        story_author = sel.xpath('//meta[@property = "article:author"]/@content').extract_first()
        story_date = sel.xpath('//meta[@property = "article:published_time"]/@content').extract_first()   
        story_keywords = sel.xpath('//meta[@name = "keywords"]/@content').extract()
        
        # The article text all comes under the "article body" - except for match reports, I think can just pull all <p>
        story_body = sel.xpath('//p//text() | //span[@class = "caption"]/text()').extract()
        
        story_text = ''.join(story_body)
        
        story_twitter = ''
        
    elif domain == 'skysports':
        # The HTMLs are a bit weird to load - looks like <p> is ok
        story_body = sel.xpath('//p[not(ancestor::ul[@class = "listblock"]) and not(@class = "site-footer__copyright")]/text()').extract()
        
        story_text = ''.join(story_body)
        
        story_twitter = ''
        story_author = ''
        story_keywords = ['']
        story_date = ''
        
    elif domain == 'telegraph':
        # HTMLs again weird - will just look for <p>s
        story_body = sel.xpath('//p//text()').extract()
        story_keywords = sel.xpath('//meta[@name = "keywords"]/@content').extract()
        story_twitter = sel.xpath('//meta[@name = "twitter:description"]/@content').extract_first()
        story_text = ''.join(story_body)
        
        story_author = ''
        story_date = ''
    
    
    # Build a dictionary of things to return - replacing mixed capitals with a space
    ## Note that this could be moved to a post treatment phase and would maybe be faster
    return_dic = {
        'story_text' : re.sub('([a-z0-9])([A-Z])', r'\1.\2', story_text),
        'story_author' : story_author,
        'story_date' : story_date,
        'story_twitter' : story_twitter,
        'story_keywords' : story_keywords,
    }
    
    return return_dic

### Saving the stories

What we really want to do is to load the pickle - look at the URL - find the HTML - then add that key to the dictionary

In [16]:
for domain in os.listdir(story_loc):
    pickle_loc = story_loc + domain + '/' + date_today + '/'
    for story_pickle in os.listdir(pickle_loc):
        pickle_path = pickle_loc + story_pickle
        print('Loading the story pickle found at \n{}'.format(story_pickle))
        
        # First load the pickle
        with open(pickle_path, 'rb') as article_file:
            article_content = pickle.load(article_file)
        
        # Then look at the URL to get the HTML path ------------------------------------------###### THERE IS AN ISSUE HERE MAYBE CHANGE THE REGEX - NOT SURE WHY SAVED AS IT DID
        valid_url = re.match('^http\S*www\.\S*$', article_content['article_link'])
        
        if valid_url and 'fake_link' not in article_content['article_link']:  
            url_extension = re.search('[^\/]\/([^\/][^www].*)', valid_url.group(0)).group(1).replace('/', '_')
            story_html = re.sub('[^A-z0-9_]+', '', url_extension)
            print('Found the link\n{}'.format(article_content['article_link']))

            # Convert into the direct location
            story_path = html_loc + domain + '/' + date_today + '/story_link/' + story_html + '.html'

            # Load the HTML
            print('Getting story for HTML located at \n{}'.format(story_path))
            with open(story_path, 'r') as story_file:
                html_content = story_file.read()

            # Then pull the info
            story_text = get_story(html_content, domain)

            # Attach to our dictionary
            article_content['story_text'] = story_text['story_text']
            article_content['story_author'] = story_text['story_author']
            article_content['story_date'] = story_text['story_date']
            article_content['story_twitter'] = story_text['story_twitter']
            article_content['story_keywords'] = story_text['story_keywords']

            # And then save it again
            print('Overwriting the pickle at \n{}'.format(story_pickle))
            with open(pickle_path, 'wb') as article_file:
                pickle.dump(article_content, article_file)
        else:
            print('The URL is not valid:\n{}'.format(article_content['article_link']))

Loading the story pickle found at 
sport_football_transfernews_crystalpalaceconfidenttyingup11830769.pickle
Found the link
https://www.mirror.co.uk/sport/football/transfer-news/crystal-palace-confident-tying-up-11830769
Getting story for HTML located at 
/home/andreas/Desktop/Projects/Football/Data/01_HTML/mirror/2018_01_27/story_link/sport_football_transfernews_crystalpalaceconfidenttyingup11830769.html
Overwriting the pickle at 
sport_football_transfernews_crystalpalaceconfidenttyingup11830769.pickle
Loading the story pickle found at 
sport_football_transfernews_josemourinhotoldrivalmanchester11905410.pickle
Found the link
https://www.mirror.co.uk/sport/football/transfer-news/jose-mourinho-told-rival-manchester-11905410
Getting story for HTML located at 
/home/andreas/Desktop/Projects/Football/Data/01_HTML/mirror/2018_01_27/story_link/sport_football_transfernews_josemourinhotoldrivalmanchester11905410.html
Overwriting the pickle at 
sport_football_transfernews_josemourinhotoldrivalma

### Testing

Let's try and load some pickles and see what they about

In [2]:
from football_functions.processes.information_extraction import stories

# There is an error and we are NOT successfully processing some links
# Specifically a lot of BBC and Mirror articles
stories.get_articles(story_loc, html_loc, date_today)

Loading the story pickle found at 
sport_football_transfernews_crystalpalaceconfidenttyingup11830769.pickle
Found the link
https://www.mirror.co.uk/sport/football/transfer-news/crystal-palace-confident-tying-up-11830769
Getting story for HTML located at 
/home/andreas/Desktop/Projects/Football/Data/01_HTML/mirror/2018_01_27/story_link/sport_football_transfernews_crystalpalaceconfidenttyingup11830769.html
Getting the story...
Loading the HTML...
Overwriting the pickle at 
sport_football_transfernews_crystalpalaceconfidenttyingup11830769.pickle
Loading the story pickle found at 
sport_football_transfernews_josemourinhotoldrivalmanchester11905410.pickle
Found the link
https://www.mirror.co.uk/sport/football/transfer-news/jose-mourinho-told-rival-manchester-11905410
Getting story for HTML located at 
/home/andreas/Desktop/Projects/Football/Data/01_HTML/mirror/2018_01_27/story_link/sport_football_transfernews_josemourinhotoldrivalmanchester11905410.html
Getting the story...
Loading the HTML

['http://www.skysports.com/fake_link/article_14',
 'http://www.skysports.com/fake_link/article_43',
 'http://www.skysports.com/fake_link/article_25',
 'http://www.skysports.com/fake_link/article_6',
 'http://www.skysports.com/fake_link/article_18',
 'http://www.skysports.com/fake_link/article_11',
 'http://www.skysports.com/fake_link/article_19',
 'http://www.skysports.com/fake_link/article_30',
 'http://www.skysports.com/fake_link/article_31',
 'http://www.skysports.com/fake_link/article_23',
 'http://www.skysports.com/fake_link/article_13',
 'http://www.skysports.com/fake_link/article_17',
 'http://www.skysports.com/fake_link/article_32',
 'http://www.skysports.com/fake_link/article_28',
 'http://www.skysports.com/fake_link/article_40',
 'http://www.skysports.com/fake_link/article_20',
 'http://www.skysports.com/fake_link/article_33',
 'http://www.skysports.com/fake_link/article_38',
 'http://www.skysports.com/fake_link/article_21',
 'http://www.skysports.com/fake_link/article_3',
 '

In [4]:
import os
i = 0
for domain in os.listdir(story_loc):
    pickle_loc = story_loc + domain + '/' + date_today + '/'
    for story_pickle in os.listdir(pickle_loc):
        i += 1
        
        if i % 100 == 0:
            pickle_path = pickle_loc + story_pickle
            print('Loading the story pickle found at \n{}'.format(story_pickle))

            # First load the pickle
            with open(pickle_path, 'rb') as article_file:
                article_content = pickle.load(article_file)
            
            for story_aspect in article_content:
                print((story_aspect, article_content[story_aspect]))

Loading the story pickle found at 
sport_football_news_nickpopefireswarningburnley11768472.pickle
('article_title', "Nick Pope fires warning to Burnley team-mate Tom Heaton - 'You'll have to fight me for No.1 spot'")
('article_link', 'https://www.mirror.co.uk/sport/football/news/nick-pope-fires-warning-burnley-11768472')
('article_summary', 'Pope has been a revelation since replacing Heaton four months ago and has kept 10 clean sheets this season')
('article_image', '/Liverpool-v-Burnley-Premier-League.jpg')
('article_date', '')
('story_text', 'Pope has been a revelation since replacing Heaton four months ago and has kept 10 clean sheets this season.Nick Pope has told Tom Heaton he will have to fight him for the No.1 spot at Burnley.Pope has been a revelation since replacing Heaton four months ago and has kept 10 clean sheets this season.Heaton is due to return from his dislocated shoulder in the new year and Pope says the Burnley skipper has helped him settle into the side.But he clai